# Preparing

In [1]:
import pandas as pd
import numpy as np
from matplotlib import cm as pltcm
import matplotlib.pyplot as plt

import os
import sys
import json
import importlib
import copy
import time

from IPython import display
import ipywidgets as widgets
from ipywidgets import interact, interact_manual

import plotly.express as px
%matplotlib inline

In [2]:
with open('./paths', 'r') as f:
    globals().update(json.loads(f.read()))

In [3]:
sys.path.append(path_Modules_Product_)
sys.path.append(path_Modules_Toolbox_)

In [4]:
datasets_path = '../Data/processed/dataset/'
dss = ['main', 'pnas', 'OOB_C']
ds_alias = {'train': 'main', 'valid': 'pnas', 'test': 'OOB_C'}
# =============
datasets = {}
for i in dss:
    datasets[i] = pd.read_csv(f'{datasets_path}ds_{i}.csv', index_col=0)
# =============
datasets['OOB_C']['p_HE4'] = datasets['OOB_C'].p_HE4_L.values
datasets['OOB_C']['s_Sex'] = 'F'
# =============
for i in datasets.keys():
    datasets[i]['s_Sex'] = datasets[i]['s_Sex'].replace(['M', 'F'], [0, 1])

# Inspection

## PCA

In [42]:
from sklearn.decomposition import PCA

In [43]:
marker = ['p_CA125', 'p_CA19-9', 'p_CA15-3', 'p_PROLACTIN', 'p_OPN', 'p_HE4']
demo = ['s_Age', 's_Sex']

In [44]:
ds_ = []
for i in datasets.keys():
    ds_.append(datasets[i][demo + marker + ['s_Tumor']].copy())
    ds_[-1]['ds'] = i
ds_ = pd.concat(ds_, ignore_index=True).dropna()
ds_['grp'] = 'affected'
ds_.loc[ds_.s_Tumor == 'Normal', 'grp'] = 'normal'

<h3>All</h3>

In [8]:
rep = pd.DataFrame(index=ds_.index, columns=['PCA1', 'PCA2', 'grp', 'ds'])
rep[['grp', 'ds']] = ds_[['grp', 'ds']].copy()
rep['label'] = rep['grp'] + '_' + rep['ds']
# =============
rep[['PCA1', 'PCA2']] = PCA(2, whiten=True).fit_transform(ds_[marker + demo])
rep[['PCA1', 'PCA2']] = rep[['PCA1', 'PCA2']].astype(float)
rep = rep.sort_values('label')
px.scatter(rep, x='PCA1', y='PCA2', color='label')

<h3>One by One</h3>

In [46]:
rep = pd.DataFrame(index=ds_.index, columns=['PCA1', 'PCA2', 'grp', 'ds'])
rep[['grp', 'ds']] = ds_[['grp', 'ds']].copy()
rep['label'] = rep['grp'] + '_' + rep['ds']
# =============
for i,d in ds_.groupby('ds'):
    rep.loc[rep.ds==i,['PCA1', 'PCA2']] = PCA(2, whiten=True).fit_transform(d[marker + demo])
rep[['PCA1', 'PCA2']] = rep[['PCA1', 'PCA2']].astype(float)
rep = rep.sort_values('label')
px.scatter(rep, x='PCA1', y='PCA2', color='label')

## Condition plot

In [15]:
marker = ['p_CA125', 'p_CA19-9', 'p_CA15-3', 'p_PROLACTIN', 'p_OPN', 'p_HE4']
demo = ['s_Age', 's_Sex']

In [35]:
ds_ = []
for i in datasets.keys():
    ds_.append(datasets[i][demo + marker + ['s_Tumor']].copy())
    ds_[-1]['ds'] = i
ds_ = pd.concat(ds_, ignore_index=True).dropna()
ds_[marker] = np.log(ds_[marker])
ds_['grp'] = 1
ds_.loc[ds_.s_Tumor == 'Normal', 'grp'] = 0
ds_.ds = ds_.ds.astype('category').cat.codes
# =============
px.parallel_coordinates(ds_, marker + demo + ['ds', 'grp'], color='ds')